# 【项目008】卷积神经网络的结构设计与实现（学生版） <span style="font-size:16px;"><a href="Project008ArchitechtureDesign.html">教学版</a> | <a href="http://deeplearning.ouxinyu.cn">返回首页</a></span> 

<span style="color:blue;">作者：欧新宇（Xinyu OU）</span>     
<span style="color:blue;">当前版本：Release v2.0 </span>   
<span style="color:blue;">开发平台：Paddle 2.5.2</span>  
<span style="color:blue;">运行环境：Intel Core i7-7700K CPU 4.2GHz, nVidia GeForce GTX 1080 Ti</span>  

<span style="color:red;">本教案所涉及的数据集仅用于教学和交流使用，请勿用作商用。</span>

**最后更新：2024年5月26日**

---

<span style="color:gray;">随着网络的加深，卷积神经网络的设计变得越来越复杂。但是，仔细观察可以发现有一些层的结构是规律的，例如Resnet结构，Inception结构等。下面我们将从最简单的**LeNet-5**和**CIFAR-10**开始，简要说明如何在Paddle中进行CNN网络结构的设计与实现。由于从飞桨框架2.5版本开始，`paddle.fluid` 库已被废弃，因此，本教案仅使用Paddle2.0+中推荐的 `paddle.nn` 库进行实现。若想浏览Paddle早期使用 `paddle.fluid` 进行库构建的方法，请访问 <a href="../../Html/Projects/Release/Project008ArchitechtureDesignTeachingV1.0.html" target="_blank">【项目008】的V1.0版本</a>。  </span>

## 【实验目的】
1. 熟悉卷积神经网络的基本结构，特别是卷积层+激活函数+池化层的叠加结构
2. 学会计算卷积神经网络各层的超参数
3. 学会根据网络结构图实现CNN类的定义
4. 学会编写代码实现CNN类的基本测试
5. 学会基于Paddle 2.0（paddle.nn）框架的设计模式

## 【实验要求】  
1. <span style='color:red;font-weight:bold;'>所有作业均在AIStudio上进行提交，提交时包含源代码和运行结果</span>
2. 按照给定的**MNIST**和**CIFAR-10**网络的拓扑结构图，完成`网络参数配置表`（**Q1, Q4**）（每个模型20分）
3. 根据`网络拓扑结构结构图`和`参数配置表`，完成MNIST神经网络类`Class MNIST()` **Q2**和CIFAR神经网络类`Class CIFAR10`**Q5**的定义（每个模型20分）
4. 完善`网络结构测试代码`和`前向传输测试代码`（**Q3, Q6**）（每个模型10分）

## 【知识准备】

在Paddle1.8的设计模式中，Paddle使用包括卷积层Conv2D，池化层Pool2D，全连接层Linear在内的三个类来实现不同的功能层，在这些功能层中使用`act`属性来定义激活函数；但是，在Paddle2.0之后的版本中，Paddle将ReLu, Sigmoid等激活函数从层的定义中移除，并定义了单独类来进行描述。此外，在Paddle 2.0之后的版本中，动态图模式被作为默认模式启用，同时取消了 `paddle.fluid` 类，而是改用 `paddle.nn` 类来实现对各个功能层的定义。与此同时，Paddle提供了一个 `paddle.vision.models` 类，并内置了LeNet, AlexNet, MobileNetV1, V2, ResNet, VGG, DenseNet等经典模型。如果不需要对模型进行修改，则可以使用Paddle的高阶API实现模型的快速调用。

### 1. Paddle 2.0 设计模式**

```python{.line-numbers}
class paddle.nn.ReLU()
class paddle.nn.Sigmoid()
class paddle.nn.Dropout(p=0.5)
class paddle.nn.Conv2D(in_channels, out_channels, kernel_size, stride=1, padding=0, dilation=1, groups=1, padding_mode='zeros', weight_attr=None, bias_attr=None, data_format='NCHW')
class paddle.nn.MaxPool2D(kernel_size, stride=None, padding=0, ceil_mode=False, return_mask=False, data_format='NCHW', name=None)
class paddle.nn.Linear(in_features, out_features, weight_attr=None, bias_attr=None, name=None)
```

- [paddle.nn.ReLU](https://www.paddlepaddle.org.cn/documentation/docs/zh/api/paddle/nn/ReLU_cn.html)
- [paddle.nn.Sigmoid](https://www.paddlepaddle.org.cn/documentation/docs/zh/api/paddle/nn/Sigmoid_cn.html)
- [paddle.nn.Dropout](https://www.paddlepaddle.org.cn/documentation/docs/zh/api/paddle/nn/Dropout_cn.html)
- [paddle.nn.MaxPool2D](https://www.paddlepaddle.org.cn/documentation/docs/zh/api/paddle/nn/MaxPool2D_cn.html)
- [paddle.nn.Conv2D](https://www.paddlepaddle.org.cn/documentation/docs/zh/api/paddle/nn/Conv2D_cn.html)
- [paddle.nn.Linear](https://www.paddlepaddle.org.cn/documentation/docs/zh/api/paddle/nn/Linear_cn.html)

### 2. Paddle高阶API

```ptython {.line-numbers}
import paddle
AlexNet = paddle.vision.models.AlexNet
model = AlexNet()
paddle.summary(model, (2, 3, 227, 227))
```

- [paddle.vision](https://www.paddlepaddle.org.cn/documentation/docs/zh/api/paddle/vision/Overview_cn.html)

## **【实验内容】**  

### **【任务一】 MNIST模型（Paddle 1.8）（50分）**

LeNet-5模型的原始输入尺寸是32×32，但是由于MNIST数据集的样本为28×28，因此需要对LeNet-5进行一定的调整。此次我们暂定调整后的模型命名为MNIST。

<img alt='Project00803MNIST' src="../../Images/Projects/Project008ArchitechtureDesign/Project00803MNIST.png" width="600">

#### **Q1: 根据LeNet-5拓扑结构图完成下列网络参数配置表(Conv1~FC2)（20分）**

- **网络参数配置表**

|Layer|Input|Kernels_num|Kernels_size|Stride|Padding|PoolingType|Output|Parameters|
|:----:|:----:|:----:|:----:|:----:|:----:|:----:|:----:|:----:|
|Input|1×28×28||||||1×28×28||
|Conv1| | | | | | | | |
|Pool1| | | | | | | | |
|Conv2| | | | | | | | |
|Pool2| | | | | | | | |
|Conv3| | | | | | | | |
|FC1| |-|-|-|-|-| | |
|FC2| |-|-|-|-|-| | |
|Output|84×1||||||10×1||
|||||||||Total = 44426|

#### **Q2: 根据LeNet-5拓扑结构图和Q1中完成的网络参数配置表完成下列MNIST模型的类定义([Your codes 1], [Your codes 2])（20分）**

- **定义神经网络类**

In [1]:
# 载入基础库
import paddle
from paddle.nn import Sequential, Conv2D, MaxPool2D, Linear, ReLU

class MNIST(paddle.nn.Layer):
    def __init__(self, num_classes=10):
        super(MNIST, self).__init__()
        # Q2-1: 根据LeNet-5拓扑结构图和Q1中完成的网络参数配置表完成下列MNIST模型的类定义
        # 各层超参数定义: [Your codes 1]
        self.features = Sequential(



        )
        self.fc = Sequential(
            # conv3层输出通道数为120


            # 在最后一个全连接层如果不定义激活函数act='softmax'，可以直接在最后的输出层定义激活函数

        )
        
    def forward(self, inputs):
        # Q2-2: 根据LeNet-5拓扑结构图和Q1中完成的网络参数配置表完成下列MNIST模型的类定义
        # 定义前向传输过程: [Your codes 2]



        return x
    

#### **Q3: 完善下列网络结构测试代码([Your codes 3])（10分）**

In [2]:
# Q3: 完善下列网络结构测试代码 [Your codes 3]



---------------------------------------------------------------------------
 Layer (type)       Input Shape          Output Shape         Param #    
   Conv2D-1      [[10, 1, 28, 28]]     [10, 6, 24, 24]          156      
    ReLU-1       [[10, 6, 24, 24]]     [10, 6, 24, 24]           0       
  MaxPool2D-1    [[10, 6, 24, 24]]     [10, 6, 12, 12]           0       
   Conv2D-2      [[10, 6, 12, 12]]      [10, 16, 8, 8]         2,416     
    ReLU-2        [[10, 16, 8, 8]]      [10, 16, 8, 8]           0       
  MaxPool2D-2     [[10, 16, 8, 8]]      [10, 16, 4, 4]           0       
   Conv2D-3       [[10, 16, 4, 4]]     [10, 120, 1, 1]        30,840     
    ReLU-3       [[10, 120, 1, 1]]     [10, 120, 1, 1]           0       
   Linear-1         [[10, 120]]            [10, 84]           10,164     
    ReLU-4           [[10, 84]]            [10, 84]              0       
   Linear-2          [[10, 84]]            [10, 10]             850      
Total params: 44,426
Trainable param

{'total_params': 44426, 'trainable_params': 44426}

### **【任务二】 CIFAR10模型（50分）**

<a href="http://www.cs.toronto.edu/~kriz/cifar.html" target="_blank">CIFAR-10</a> 是由 Hinton 的学生 Alex Krizhevsky 和 Ilya Sutskever 整理的一个用于识别普适物体的小型数据集，该数据集的所有样本均从 <a href="http://people.csail.mit.edu/torralba/tinyimages/" target="_blank">80 million tiny images</a> 数据中获取。一共包含10 个类别的RGB彩色图片：飞机（ airplane ）、汽车（ automobile ）、鸟类（ bird ）、猫（ cat ）、鹿（ deer ）、狗（ dog ）、蛙类（ frog ）、马（ horse ）、船（ ship ）和卡车（ truck ）。每个图片的尺寸为32 × 32，每个类别有6000个图像，数据集中一共有50000 张训练图片和10000 张测试图片。此外还有一个与CIFAR-10类似的CIFAR-100数据集，也由Alex和Ilya收集，该数据包含100个类，每个类100个样本，其中500个用于训练，100个用于测试。

下图是一个经典的用于CIFAR-10识别的卷积神经网络结构图。

<img alt='Project00804CIFAR10' src="../../Images/Projects/Project008ArchitechtureDesign/Project00804CIFAR10.png" width="600">

#### **Q4: 根据CIFAR-10拓扑结构图完成下列网络参数配置表（Conv1~FC2）（20分）**

- **网络参数配置表**

|Layer|Input|Kernels_num|Kernels_size|Stride|Padding|PoolingType|Output|Parameters|
|:----:|:----:|:----:|:----:|:----:|:----:|:----:|:----:|:----:|
|Input|3×32×32||||||3×32×32|
|Conv1| | | | | | | | |
|Pool1| | | | | | | | |
|Conv2| | | | | | | | |
|Pool2| | | | | | | | |
|Conv3| | | | | | | | |
|Pool3| | | | | | | | |
|FC1| |-|-|-|-|-| | |
|FC2| |-|-|-|-|-| | |
|Output|||||||10×1||
|||||||||Total = 65706|

#### **Q5: 根据Cifar10拓扑结构图和Q4中完成的网络参数配置表完成下列Cifar10模型的类定义([Your codes 6], [Your codes 7])（20分）**

- **定义神经网络类**

In [3]:
# 载入基础库
import paddle
from paddle.nn import Sequential, Conv2D, MaxPool2D, AvgPool2D, Linear, Dropout, ReLU

class Cifar10(paddle.nn.Layer):
    def __init__(self, num_classes=10):
        super(Cifar10, self).__init__()
        self.num_classes = num_classes
        # Q5-1: 根据Cifar10拓扑结构图和Q4中完成的网络参数配置表完成下列Cifar10模型的类定义
        # 各层超参数定义: [Your codes 4]
        self.features = 
        
        
        
        )
        self.fc = Sequential(
            
            
        )
        
    def forward(self, inputs):
        # Q5-2: 根据Cifar10拓扑结构图和Q4中完成的网络参数配置表完成下列Cifar10模型的类定义
        # 定义前向传输过程: [Your codes 5]

        
        
        
        return x

#### **Q6: 完善下列网络结构测试代码([Your codes 8], [Your codes 9])和前向传输测试代码([Your codes 10])（10分）**

- **网络结构测试**

In [4]:
#### 网络测试
if __name__ == '__main__':
    # 1. 输出网络结构
    # Q6-1: 完善下列网络结构测试代码: [Your codes 6]

    
    
    
    # 2. 测试前向传输
    # Q6-2: 完善前向传输测试代码: [Your codes 7]
    print('测试前向传输:')

    
    
    print(outs)
    print('输出张量的形态为:{}'.format(outs.shape))

---------------------------------------------------------------------------
 Layer (type)       Input Shape          Output Shape         Param #    
   Conv2D-4       [[1, 3, 32, 32]]     [1, 32, 28, 28]         2,432     
    ReLU-5       [[1, 32, 28, 28]]     [1, 32, 28, 28]           0       
  MaxPool2D-3    [[1, 32, 28, 28]]     [1, 32, 14, 14]           0       
   Conv2D-5      [[1, 32, 14, 14]]     [1, 32, 10, 10]        25,632     
    ReLU-6       [[1, 32, 10, 10]]     [1, 32, 10, 10]           0       
  AvgPool2D-1    [[1, 32, 10, 10]]      [1, 32, 5, 5]            0       
   Conv2D-6       [[1, 32, 5, 5]]       [1, 64, 2, 2]         32,832     
    ReLU-7        [[1, 64, 2, 2]]       [1, 64, 2, 2]            0       
  AvgPool2D-2     [[1, 64, 2, 2]]       [1, 64, 1, 1]            0       
   Linear-3          [[1, 64]]             [1, 64]             4,160     
   Linear-4          [[1, 64]]             [1, 10]              650      
Total params: 65,706
Trainable param

### 【任务三】 AlexNet模型（拓展练习）

**AlexNet模型**[1]，由多伦多大学的Geffery Hinton教授的学生Krizhevsky Alex提出，下面使用Paddle2.0的Paddle.nn库进行网络拓扑结构的设计。

*[1] Alex Krizhevsky, Ilya Sutskever, Geoffrey E. Hinton. ImageNet classification with deep convolutional neural networks. International Conference on Neural Information Processing Systems. Curran Associates Inc. 2012:1097-1105.*

### 3.1 网络拓扑结构图

<img alt="Project00802AlexNet" src="../../Images/Projects/Project008ArchitechtureDesign/Project00802AlexNet.png" width="800px">

<span style="color:blue;">需要注意的是，在大多数深度学习工具包中，Alexnet的输入尺度会被Crop为 [3×227×227]。如果按照原始论文中 [3×224×224] 的尺度进行输入，需要适当调节网络的参数<span>

    Conv: Output_size = (Input_size - Kernel_size + 2\*Padding)/Stride + 1  
    Pool: Output_size = Input_size/Stride.

（以下内容请读者自行完成）

建议框架：

### 3.2 网络参数配置表

根据网络拓扑结构图定义网络参数配置表，以便于对神经网络类进行定义。

### 3.3 定义神经网络类

神经网络定义可以使用三种方法，分别是逐层定义、模块化定义（使用`Sequential`库）和继承定义（Paddle高阶API）。

#### 3.3.1 逐层定义

### 3.4 网络测试

#### 3.4.1 网络结构测试

使用 `Paddle.summary()` 方法对模型进行结构信息输出。值得注意的是Paddle.vision.models.AlexNet所定义的AlexNet模型与论文中原始的模型有细微差异，有兴趣的同学可以使用 `print(model)` 方法将模型配置进行输出对比。

#### 3.4.2 前向传输测试

定义一个随机输入，并使用 `model(input)` 方法进行前向传输，输出结果。
